In [55]:
import matplotlib.pyplot as plt
import random as r
import pprint as pp
import numpy as np
import csv
import tensorflow as tf
from tensorflow import keras


In [56]:
# Define slice types and parameters
slices_type = {
    'eMBB' : {
       #'bandwidth_max': 100000000, #max bandwidth which BS can give to this slice
        'client_weight': 0.3, # Portion of clients which use this type of slice
        'band_guaranteed' : 0, # based on quality of service
        'min': 4000000, 
        'max': 500000000 # how much bps can require this type of slice
      },
      'URLLC' : {
       #'bandwidth_max': 10000000,
        'client_weight': 0.2,
        'band_guaranteed' : 5000000,
        'min': 800,
        'max': 8000000
      },
      'MIoT' : {
       #'bandwidth_max': 10000000,
        'client_weight': 0.15,
        'band_guaranteed' : 1000000,
        'min': 800000, 
        'max': 8000000
      },
      'mMTC' : {
       #'bandwidth_max': 10000000,
        'client_weight': 0.15,
        'band_guaranteed' : 1000000,
        'min': 800000, 
        'max': 8000000
      },
      'voice' : {
       #'bandwidth_max': 1000000,
        'client_weight': 0.2,
        'band_guaranteed' : 500000,
        'min': 4000000, 
        'max': 8000000
     }
}
          
# Define base station parameters
basestation = {
    'capacity': 20000000000,   #20Gbps
    'coverage': 250,
    'ratios': { # portion of capacity dedicated to various slice type
        'URLLC': 0.05,
        'eMBB': 0.55,
        'mMTC': 0.15,
        'voice': 0.1,
        'MIoT': 0.15
    },
    'x': 300,
    'y': 300
}

# Define mobility patterns and parameters
mobility_patterns = {
  'car': {
    'distribution': 'normal',
    'params':(0,7),
    'client_weight': 0.10
  },
  'walk': {
    'distribution': 'randint',
    'params': (-1, 1),
    'client_weight': 0.40
  },
  'stationary': {
    'distribution': 'normal',
    'params': (0, 0.1),
    'client_weight': 0.20
  },
  'publictransport': {
    'distribution': 'randint',
    'params': (-4, 4),
    'client_weight': 0.10
  },
  'slackperson':{
    'distribution': 'randint',
    'params':(0, 1),
    'client_weight': 0.20
  }
}

In [57]:
# Define obj Client
class Client:
    def __init__(self, ID, x, y, mobility_pattern, freq, slice_type, bs, slice_cap = None):
        self.ID = ID
        self.x = x
        self.y = y
        self.mobility_pattern = mobility_pattern
        self.freq = freq
        self.slice_type = slice_type
        self.bs = bs
       #self.slice_cap = slice_cap
        self.usage_rem = 0
        self.last_usage = 0
        self.connected = False
        
        # stats
        self.tot_connected_time = 0
        self.tot_unconnected_time = 0
        self.tot_requests = 0
        self.consume_time = 0
        self.tot_usage = 0
        
    def step_1(self):
        if self.bs is not None:
            if self.usage_rem > 0:
                if self.connected:
                    self.start_consume()
                else:
                    self.connect()
            else:
                if self.connected:
                    self.disconnect()
                else:
                    self.generate_usage_and_connect()
        
    def step_2(self):
        if self.connected and self.last_usage > 0:
            self.release_consume()
            if self.usage_rem == 0:
                self.disconnect()
    
    def step_3(self):
        x, y = self.move()
        self.x += x
        self.y += y
        if self.bs is not None:
            if not inRange(self, bs):
                self.disconnect()       
                
    def generate_usage_and_connect(self):
        if self.slice_type is not None:
            # Generate new usage
            self.usage_rem = self.generate()
            self.tot_requests += 1
            self.connect()
            print(f"Client_{self.ID}, coordinates : ({self.x}, {self.y}) requests {self.usage_rem} usage to BS{self.bs.ID}")     

    def connect(self):
        s = self.slice_type
        if self.connected:
            return
        if self.is_avaliable():         # threshold for usage
            self.connected = True
            bs.connected_users += 1
            print(f"Client {self.ID}, coordinates : ({self.x}, {self.y}) connected to slice {s} @ BS{self.bs.ID}")
            return True
        else:
            self.connected = False
            print(f"Client {self.ID}, coordinates : ({self.x}, {self.y}) connection refused to slice {s} @ BS{self.bs.ID}")
            return False
        
    def disconnect(self):
        if self.connected == True:
            bs.connected_users -= 1
            self.connected = False
        print(f"Client {self.ID}, coordinates: ({self.x},{self.y}) disconnected from slice {self.slice_type} @ BS{self.bs.ID} ")
        return not self.connected
    
    def start_consume(self):
        amount = min(self.usage_rem, self.get_consumable_share())    # bandwidth allocation
        bs.band_remaining -= amount  # BS allocate bandwidth and its capacity decreases
        bs.pot_band_remaining -= amount
        self.last_usage = amount
        print(f"Client {self.ID}, coordinates: ({self.x}, {self.y}) gets {amount} usage from @ BS{self.bs.ID}")
           
    def release_consume(self):
        # release resources
        if self.last_usage > 0:
            bs.band_remaining += self.last_usage
            self.consume_time += 1
            self.tot_usage += self.last_usage
            self.usage_rem -= self.last_usage
            print(f"Client {self.ID}, coordinates: ({self.x}, {self.y}), releases {self.last_usage} usage to BS{self.bs.ID}")
            self.last_usage = 0
        
    # update client coordinates    
    def move(self):   
        distr = self.mobility_pattern.distribution
        params = self.mobility_pattern.params
        if distr == "randint":
            delta_x = r.randint(params[0], params[1])
            delta_y = r.randint(params[0], params[1])
            return delta_x, delta_y
        if distr == "normal":
            delta_x = np.random.normal(params[0], params[1])
            delta_y = np.random.normal(params[0], params[1])
            return delta_x, delta_y 
        
    # generate client consume   
    def generate(self):
        s = self.slice_type
        amount = r.randint(slices_type[s]['min'], slices_type[s]['max'])
        return amount
    
    def is_avaliable(self):
        global client_per_slice
        global new_capacity
        s = self.slice_type
        bandwidth_next = new_capacity[s] / (client_per_slice[s] + 1)
        if bandwidth_next < slices_type[s]['band_guaranteed']:
            return False
        return True
      
    def get_consumable_share(self):
        global client_per_slice
        global new_capacity
        s = self.slice_type

        if client_per_slice.get(s) <= 0:
            return int(new_capacity[s])
        else:
            return int(new_capacity[s]/client_per_slice[s])   
        

In [58]:
# Define obj Mobility 
class Mobility:
    def __init__(self, name, distribution, params):
        self.name = name
        self.distribution = distribution
        self.params = params

In [59]:
# Define obj BaseStation
class BaseStation:
    def __init__(self,ID, x, y, coverage, capacity, ratios):
        self.ID =ID
        self.x = x
        self.y = y
        self.coverage = coverage
        self.capacity = capacity
        self.ratios = ratios
        self.pot_band_remaining = capacity
        self.band_remaining = capacity
        self.connected_users = 0

In [60]:
def get_random_mobility_pattern(vals, mobility_patterns):
    i = 0
    j = r.random()

    while vals[i] < j:
        i += 1

    return mobility_patterns[i]


def get_random_slice_type(vals):
    i = 0
    j = r.random()
    s = ''

    while vals[i] < j:
        i += 1
    
    if i == 0:
       s = 'eMBB'
    if i == 1:
       s = 'URLLC' 
    if i == 2:
       s = 'MIoT' 
    if i == 3:
       s = 'mMTC' 
    if i == 4:
       s = 'voice' 
    
    return s

def get_number_user_slice_type(all_client):
    embb = 0
    miot = 0
    mmtc = 0
    voice = 0 
    urllc = 0
    
    for c in all_client:
        if c.slice_type == 'eMBB':
            embb = embb + 1

        if c.slice_type == 'URLLC':
            urllc = urllc + 1

        if c.slice_type == 'MIoT':
            miot = miot + 1

        if c.slice_type == 'mMTC':
            mmtc = mmtc + 1

        if c.slice_type == 'voice':
            voice = voice + 1
    
    user_per_slice = {'eMBB': embb,
                      'URLLC': urllc,
                      'MIoT': miot,
                      'mMTC': mmtc,
                      'voice': voice
                     }
    
    return user_per_slice

def get_new_ratios(prediction):
    # Rescale to 19 Gbit
    band = basestation.get('capacity') - 1000000000
    total_prediction = sum(prediction)
    
    # Compute new cpacity
    embb = int(prediction[0]*band)/total_prediction
    urllc = int(prediction[1]*band)/total_prediction
    miot = int(prediction[2]*band)/total_prediction
    mmtc = int(prediction[3]*band)/total_prediction
    voice = int(prediction[4]*band)/total_prediction

    out = { 'eMBB': embb,
            'URLLC': urllc,
            'MIoT': miot,
            'mMTC': mmtc,
            'voice': voice
          }
    
    return out

def inRange(client, bs):
    x_client = client.x
    y_client = client.y
    x_bs = bs.x
    y_bs = bs.y
    if (abs(x_client - x_bs) < bs.coverage) and (abs(y_client - y_bs) < bs.coverage):
        return True
        print('true')
    else:
        return False
        print('false')

collected, slice_weights = 0, []
for key, value in slices_type.items():
    collected += value['client_weight']
    slice_weights.append(collected)

collected, mb_weights = 0, []
for key, value in mobility_patterns.items():
    collected += value['client_weight']
    mb_weights.append(collected)
    
m_patterns = []
for name, mb in mobility_patterns.items():
    mobility_pattern = Mobility(name, mb['distribution'], mb['params'])
    m_patterns.append(mobility_pattern)   
    
# Load RNN
model = tf.keras.models.load_model('model.h5')


In [61]:
# Define class Request
class Request:
    def __init__(self, id_client, type_slice, traffic_request, traffic_left):
        self.id_client = id_client
        self.type_slice = type_slice
        self.traffic_request = traffic_request
        self.traffic_left = traffic_left
        
#Define class csv
class CsvData:
    def __init__(self, step, r_embb, g_embb, connect_embb, r_urllc, g_urllc, connect_urllc, r_miot, g_miot, connect_miot, r_mmtc, g_mmtc, connect_mmtc, r_voice, g_voice, connect_voice):
        self.step = step
        self.r_embb = r_embb
        self.g_embb = g_embb
        self.connect_embb = connect_embb
        self.r_urllc = r_urllc
        self.g_urllc = g_urllc
        self.connect_urllc = connect_urllc
        self.r_miot = r_miot
        self.g_miot = g_miot
        self.connect_miot = connect_miot
        self.r_mmtc = r_mmtc
        self.g_mmtc = g_mmtc
        self.connect_mmtc = connect_mmtc
        self.r_voice = r_voice
        self.g_voice = g_voice
        self.connect_voice = connect_voice
        

In [62]:
# Round 0: create network area, place base station and clients
num_clients = 500
simulation_time = 100
x_area = 600
y_area = 600

bs = BaseStation(0, basestation.get('x'), basestation.get('y'), basestation.get('coverage'), basestation.get('capacity'), basestation.get('ratios'))

clients = []
for i in range(num_clients):
    x = r.randint(0, x_area)
    y = r.randint(0, y_area)
    freq = r.random()
    
    mobility_pattern = get_random_mobility_pattern(mb_weights, m_patterns)
    slice_type = get_random_slice_type(slice_weights) 
    #slice_capacity = bs.ratios.get(slice_type) * bs.capacity
    
    c = Client(i, x, y, mobility_pattern, freq, slice_type, bs)
    clients.append(c)


In [63]:
clients_inRange = []

for i in range(num_clients):
    if inRange(clients[i], bs):
        clients_inRange.append(clients[i])

# create fixed size list to manage the request
request_list = [None] * len(clients)
active_clients = []
csv_final = []

for n in range(simulation_time):
    
    # manage number active clients
    active = []
    new_connection = r.randint(0, len(clients_inRange))
    active = r.sample(clients_inRange, new_connection)
    
    for j in range(len(active)):
        if request_list[active[j].ID] == None:
            active_clients.append(active[j])
            
    client_per_slice = get_number_user_slice_type(active_clients)
    
    if n > 2:
        new_ratios = [[[req_embb, req_urllc, req_miot, req_mmtc, req_voice]]]
        #print(new_ratios)
        new_ratios = np.array(new_ratios)/bs.capacity
        prediction = model.predict(new_ratios)
        #print(prediction[0])
        
        # TODO: implement function below (new capacity must be a DICTIONARY)
        new_capacity = get_new_ratios(prediction[0])
        #print(new_capacity)
    else:    
        # here put the ratios standard predefined
        new_capacity = {'eMBB':  13000000000,
                        'URLLC': 1000000000,
                        'MIoT':  2000000000,
                        'mMTC':  2000000000,
                        'voice': 2000000000
                       }
    
    print('STEP', n)
    
    for i in range(len(active_clients)):   
        # step 1 and create request
        active_clients[i].step_1()
        
        req = Request(active_clients[i].ID, active_clients[i].slice_type, active_clients[i].usage_rem, active_clients[i].usage_rem)
        request_list[active_clients[i].ID] = req
    
    for i in range(len(active_clients)):
        # step 2 and update request (delete non active user, and update traffic)
        active_clients[i].step_2()
        request_list[active_clients[i].ID].traffic_left = active_clients[i].usage_rem
    
    user_embb, user_urllc, user_miot, user_mmtc, user_voice = 0, 0, 0, 0, 0
    req_embb, req_urllc, req_miot, req_mmtc, req_voice = 0, 0, 0, 0, 0
    giv_embb, giv_urllc, giv_miot, giv_mmtc, giv_voice = 0, 0, 0, 0, 0
    for item in request_list:
     if item is not None:
        if item.type_slice == 'eMBB':
            if item.traffic_request - item.traffic_left != 0:
                req_embb += item.traffic_request
                giv_embb += item.traffic_request - item.traffic_left
                user_embb += 1   
            else:
                req_embb += 0
                giv_embb += 0
                user_embb += 1   
        if item.type_slice == 'URLLC' :
            if item.traffic_request - item.traffic_left != 0:
                req_urllc += item.traffic_request
                giv_urllc += item.traffic_request - item.traffic_left
                user_urllc += 1
            else:
                req_urllc += 0
                giv_urllc += 0
                user_urllc += 1   
        if item.type_slice == 'MIoT':
            if item.traffic_request - item.traffic_left != 0:
                req_miot += item.traffic_request
                giv_miot += item.traffic_request - item.traffic_left
                user_miot += 1
            else:
                req_miot += 0
                giv_miot += 0
                user_miot += 1   
        if item.type_slice == 'mMTC':
            if item.traffic_request - item.traffic_left != 0:
                req_mmtc += item.traffic_request
                giv_mmtc += item.traffic_request - item.traffic_left
                user_mmtc += 1
            else:
                req_mmtc += 0
                giv_mmtc += 0
                user_mmtc += 1   
        if item.type_slice == 'voice':
            if item.traffic_request - item.traffic_left != 0:
                req_voice += item.traffic_request
                giv_voice += item.traffic_request - item.traffic_left
                user_voice += 1   
            else:
                req_voice += 0
                giv_voice += 0
                user_voice += 1 
    
    # we can remove this 2 lines 
    csv_data = CsvData(n, req_embb, giv_embb, user_embb, req_urllc, giv_urllc, user_urllc, req_miot, giv_miot, user_miot, req_mmtc, giv_mmtc, user_mmtc, req_voice, giv_voice, user_voice)  
    csv_final.append(csv_data)
    
    for i in range(len(active_clients)):
        if active_clients[i].connected == False:
            request_list[active_clients[i].ID] = None

    for item in active_clients:
        # step 3 and delete also user not in range
        item.step_3()
        if item.connected == False:
            request_list[item.ID] = None
            active_clients.remove(item)
            

STEP 0
Client 417, coordinates : (444, 255) connected to slice eMBB @ BS0
Client_417, coordinates : (444, 255) requests 101223149 usage to BS0
Client 67, coordinates : (423, 262) connected to slice voice @ BS0
Client_67, coordinates : (423, 262) requests 6193261 usage to BS0
Client 269, coordinates : (93, 238) connected to slice mMTC @ BS0
Client_269, coordinates : (93, 238) requests 6504447 usage to BS0
Client 188, coordinates : (335, 146) connected to slice URLLC @ BS0
Client_188, coordinates : (335, 146) requests 3828578 usage to BS0
Client 124, coordinates : (422, 277) connected to slice URLLC @ BS0
Client_124, coordinates : (422, 277) requests 980963 usage to BS0
Client 109, coordinates : (271, 505) connected to slice eMBB @ BS0
Client_109, coordinates : (271, 505) requests 135891325 usage to BS0
Client 285, coordinates : (232, 275) connected to slice mMTC @ BS0
Client_285, coordinates : (232, 275) requests 2122573 usage to BS0
Client 332, coordinates : (281, 178) connected to sli

STEP 3
Client 67, coordinates: (423, 264) gets 2689655 usage from @ BS0
Client 188, coordinates: (337, 147) gets 1531307 usage from @ BS0
Client 109, coordinates: (271, 506) gets 81984758 usage from @ BS0
Client 332, coordinates: (281, 178) gets 286175839 usage from @ BS0
Client 87, coordinates: (408.1882165975229, 197.08249591221332) gets 1970314 usage from @ BS0
Client 182, coordinates: (396, 145) gets 305062443 usage from @ BS0
Client 371, coordinates: (411, 216) gets 1739805 usage from @ BS0
Client 434, coordinates: (519, 182) gets 2092226 usage from @ BS0
Client 444, coordinates: (488, 355) gets 1970314 usage from @ BS0
Client 315, coordinates: (177.58415836181422, 104.90673125650349) gets 5057276 usage from @ BS0
Client 221, coordinates: (181, 168) gets 5057276 usage from @ BS0
Client 491, coordinates: (445, 133) gets 290321357 usage from @ BS0
Client 202, coordinates: (209, 526) gets 1970314 usage from @ BS0
Client 343, coordinates: (105, 221) gets 1970314 usage from @ BS0
Clien

STEP 5
Client 67, coordinates: (424, 265) gets 1894477 usage from @ BS0
Client 87, coordinates: (408.1882165975229, 197.08249591221332) gets 1592629 usage from @ BS0
Client 182, coordinates: (393, 145) gets 191197541 usage from @ BS0
Client 434, coordinates: (519, 182) gets 89441 usage from @ BS0
Client 444, coordinates: (490, 355) gets 1592629 usage from @ BS0
Client 221, coordinates : (184, 166) connected to slice mMTC @ BS0
Client_221, coordinates : (184, 166) requests 3899972 usage to BS0
Client 202, coordinates: (210, 527) gets 1592629 usage from @ BS0
Client 343, coordinates: (103, 224) gets 37391 usage from @ BS0
Client 410, coordinates: (138, 285) gets 1592629 usage from @ BS0
Client 27, coordinates : (506, 318) connected to slice eMBB @ BS0
Client_27, coordinates : (506, 318) requests 389051456 usage to BS0
Client 140, coordinates: (347, 497) gets 191197541 usage from @ BS0
Client 40, coordinates: (384, 388) gets 1789265 usage from @ BS0
Client 122, coordinates: (540, 108) get

Client 31, coordinates : (123.2743238554532, 195.0241588288577) connection refused to slice URLLC @ BS0
Client 42, coordinates: (539, 67) gets 191197541 usage from @ BS0
Client 324, coordinates: (220, 463) gets 191197541 usage from @ BS0
Client 14, coordinates : (132, 285) connected to slice eMBB @ BS0
Client_14, coordinates : (132, 285) requests 458680073 usage to BS0
Client 193, coordinates : (257, 86) connected to slice MIoT @ BS0
Client_193, coordinates : (257, 86) requests 3259388 usage to BS0
Client 426, coordinates : (174, 420) connected to slice voice @ BS0
Client_426, coordinates : (174, 420) requests 6510210 usage to BS0
Client 463, coordinates : (379.6584633172645, 119.35656706684469) connected to slice voice @ BS0
Client_463, coordinates : (379.6584633172645, 119.35656706684469) requests 4512949 usage to BS0
Client 397, coordinates : (480, 115) connected to slice eMBB @ BS0
Client_397, coordinates : (480, 115) requests 367714494 usage to BS0
Client 103, coordinates : (393, 

Client 194, coordinates: (512, 161) gets 2403555 usage from @ BS0
Client 32, coordinates: (544, 128) gets 200907276 usage from @ BS0
Client 62, coordinates: (485.5890265008595, 78.02169650297589) gets 3810496 usage from @ BS0
Client 199, coordinates: (78, 294) gets 3865318 usage from @ BS0
Client 276, coordinates: (322.91787635737336, 363.9025532300438) gets 2296165 usage from @ BS0
Client 42, coordinates: (539, 67) gets 197505377 usage from @ BS0
Client 324, coordinates: (219, 463) gets 76810907 usage from @ BS0
Client 14, coordinates: (131.834101352584, 284.90862538438853) gets 200907276 usage from @ BS0
Client 193, coordinates: (258, 87) gets 2086749 usage from @ BS0
Client 426, coordinates: (174, 421) gets 2296165 usage from @ BS0
Client 463, coordinates: (378.7901397892189, 123.46785809494104) gets 2296165 usage from @ BS0
Client 397, coordinates: (481, 114) gets 200907276 usage from @ BS0
Client 103, coordinates: (393, 280) gets 3865318 usage from @ BS0
Client 373, coordinates : 

...

STEP 94
Client 488, coordinates: (140, 146) gets 1006249 usage from @ BS0
Client 256, coordinates: (92.2709494030718, 439.6989526875865) gets 198562606 usage from @ BS0
Client 100, coordinates: (232, 166) gets 2045326 usage from @ BS0
Client 257, coordinates: (275, 420) gets 2296865 usage from @ BS0
Client 426, coordinates: (204, 457) gets 2296865 usage from @ BS0
Client 183, coordinates: (53, 450) gets 198562606 usage from @ BS0
Client 95, coordinates: (67, 446) gets 1946200 usage from @ BS0
Client 238, coordinates : (347, 204) connected to slice voice @ BS0
Client_238, coordinates : (347, 204) requests 7295452 usage to BS0
Client 362, coordinates : (165.66841807618624, 270.14844169265405) connected to slice MIoT @ BS0
Client_362, coordinates : (165.66841807618624, 270.14844169265405) requests 4668090 usage to BS0
Client 441, coordinates: (542, 220) gets 157605767 usage from @ BS0
Client 381, coordinates: (101, 183) gets 3413689 usage from @ BS0
Client 419, coordinates: (122.694654160

STEP 95
Client 256, coordinates: (92.2709494030718, 439.6989526875865) gets 210254205 usage from @ BS0
Client 100, coordinates: (231, 165) gets 1950719 usage from @ BS0
Client 257, coordinates: (275, 420) gets 1003202 usage from @ BS0
Client 426, coordinates: (204, 457) gets 937130 usage from @ BS0
Client 183, coordinates: (60, 447) gets 96561537 usage from @ BS0
Client 238, coordinates: (347, 204) gets 2030908 usage from @ BS0
Client 362, coordinates: (159.9321905739741, 266.70865490814094) gets 1950719 usage from @ BS0
Client 381, coordinates: (101, 183) gets 143491 usage from @ BS0
Client 419, coordinates: (122.83060171857278, 258.9984905910818) gets 882817 usage from @ BS0
Client 178, coordinates : (107, 226) connected to slice voice @ BS0
Client_178, coordinates : (107, 226) requests 4372932 usage to BS0
Client 313, coordinates: (427, 170) gets 1950719 usage from @ BS0
Client 192, coordinates: (478, 545) gets 10833 usage from @ BS0
Client 201, coordinates: (224.70162074979518, 438

Client_461, coordinates : (516.3486632568151, 351.26921364135745) requests 1988420 usage to BS0
Client 309, coordinates : (569, 530) connected to slice eMBB @ BS0
Client 223, coordinates : (368, 379) connected to slice eMBB @ BS0
Client_223, coordinates : (368, 379) requests 648620710 usage to BS0
Client 434, coordinates : (542, 202) connection refused to slice URLLC @ BS0
Client 75, coordinates : (507, 501) connection refused to slice URLLC @ BS0
Client 25, coordinates: (265, 368) gets 158240743 usage from @ BS0
Client 40, coordinates : (385, 394) connection refused to slice URLLC @ BS0
Client 381, coordinates : (98, 179) connected to slice mMTC @ BS0
Client_381, coordinates : (98, 179) requests 5213028 usage to BS0
Client 422, coordinates : (486, 320) connection refused to slice URLLC @ BS0
Client 200, coordinates: (424.0960801689732, 67.46656407340521) gets 1534141 usage from @ BS0
Client 390, coordinates : (441, 322) connected to slice mMTC @ BS0
Client_390, coordinates : (441, 322

Client 97, coordinates: (528, 229) gets 1648449 usage from @ BS0
Client 156, coordinates : (113, 435) connection refused to slice URLLC @ BS0
Client 235, coordinates: (228.11495663600675, 325.4283188477665) gets 179056919 usage from @ BS0
Client 341, coordinates: (275, 375) gets 137400827 usage from @ BS0
Client 239, coordinates: (294, 483) gets 1851365 usage from @ BS0
Client 53, coordinates: (105, 256) gets 37605069 usage from @ BS0
Client 324, coordinates: (216, 468) gets 146229409 usage from @ BS0
Client 98, coordinates: (528, 147) gets 2823345 usage from @ BS0
Client 19, coordinates: (256, 136) gets 191033360 usage from @ BS0
Client 210, coordinates: (263.6658145792454, 195.89388848483586) gets 191033360 usage from @ BS0
Client 88, coordinates: (490, 500) gets 1851365 usage from @ BS0
Client 403, coordinates : (79, 459) connection refused to slice URLLC @ BS0
Client 332, coordinates : (280, 169) connected to slice eMBB @ BS0
Client_332, coordinates : (280, 169) requests 236367667 

STEP 99
Client 426, coordinates: (208, 460) gets 686982 usage from @ BS0
Client 419, coordinates: (122.95984887565389, 258.82031991584773) gets 1982378 usage from @ BS0
Client 444, coordinates : (487, 356) connected to slice MIoT @ BS0
Client_444, coordinates : (487, 356) requests 4872781 usage to BS0
Client 447, coordinates: (142.39991099066955, 68.03180320354491) gets 3234456 usage from @ BS0
Client 467, coordinates: (105.5405909554666, 514.6358420994127) gets 1024849 usage from @ BS0
Client 182, coordinates : (419, 132) connected to slice eMBB @ BS0
Client_182, coordinates : (419, 132) requests 314935517 usage to BS0
Client 201, coordinates: (224.59354093218377, 438.3871408630927) gets 1982378 usage from @ BS0
Client 311, coordinates: (298, 381) gets 2586883 usage from @ BS0
Client 41, coordinates: (384, 200) gets 1982378 usage from @ BS0
Client 54, coordinates: (189.0825708375211, 236.20973168350068) gets 231672176 usage from @ BS0
Client 339, coordinates: (232, 475) gets 1572816 u

In [64]:
# This part can be removed
with open('input.csv', mode='w') as csv_file:
    fieldnames = ['embb_rate', 'embb_users', 'embb_req', 'urllc_rate', 'urllc_users', 'urllc_req', 'miot_rate', 'miot_users', 'miot_req', 'mmtc_rate', 'mmtc_users', 'mmtc_req', 'voice_rate', 'voice_users', 'voice_req']
    writer = csv.DictWriter(csv_file, fieldnames=fieldnames)
    
    writer.writeheader()
    for item in csv_final:
        writer.writerow({'embb_rate': item.g_embb, 'embb_users': item.connect_embb, 'embb_req': item.r_embb, 'urllc_rate': item.g_urllc, 'urllc_users': item.connect_urllc, 'urllc_req': item.r_urllc, 'miot_rate': item.g_miot, 'miot_users': item.connect_miot, 'miot_req': item.r_miot, 'mmtc_rate': item.g_mmtc, 'mmtc_users': item.connect_mmtc, 'mmtc_req': item.r_mmtc, 'voice_rate': item.g_voice, 'voice_users': item.connect_voice, 'voice_req': item.r_voice,})
    